In [442]:
import pandas as pd
import numpy as np
import os

In [443]:
computer_path = os.getcwd()
path_input_data = os.getcwd()+os.path.sep+"Data"
path_EPCs = r"D:\OneDrive - Cardiff University\04 - Projects\03 - PhD\03 - Analysis\03 - LSOAs\00 - Data\EPC and energy efficiency\all-domestic-certificates" #computer_path + os.path.sep + r"Data" +os.path.sep +r"EPCs"
saving_path = r"D:\OneDrive - Cardiff University\04 - Projects\03 - PhD\03 - Analysis\03 - LSOAs\00 - Data" #computer_path

## Input parameters

In [444]:
# specify the name of the local authorit(y/ies) you would like to calculate heat demand data for
# if no name specified, this is done for all local authorities in England and Wales.

local_authority = []
potential = True #potential variable set to True to calculate heat demand after considering energy efficiency measures

if len(local_authority)>0:
    output_file_name = "LSOAs_in_selected_LA"
else:
    output_file_name ="LSOAs_in_England_Wales"
    
if potential:
    output_file_name = output_file_name + "_after_EE_heat_demand"
else:
    output_file_name = output_file_name + "_before_EE_heat_demand"


### Import lookup table linking posctode, LSOA, MSOA and Region

In [445]:
OA_lookup_file = r"PCD11_OA11_LSOA11_MSOA11_LAD11_EW_LU_feb_2018.csv"
OA_lookup_df = pd.read_csv(path_input_data+os.path.sep+OA_lookup_file, low_memory=False)
OA_lookup_df.drop(["pcd8", "pcds", "dointr", "doterm", "usertype", "lsoa11nm", "msoa11nm","ladnmw", "FID"], axis=1, inplace=True) 
OA_lookup_df.drop_duplicates(inplace=True)

region_lookup_file = r"laregionlookup376las.xls"
region_lookup_df = pd.read_excel(path_input_data+os.path.sep+region_lookup_file, sheet_name=1, header=6, usecols=[0, 1, 3])

OA_lookup_df = pd.merge(OA_lookup_df, region_lookup_df, left_on='ladcd', right_on='la_code', how='left')

OA_lookup_df = pd.merge(OA_lookup_df, region_lookup_df, left_on='ladnm', right_on='la_name', how='left')
OA_lookup_df["la_code_x"].fillna(OA_lookup_df["la_code_y"], inplace=True)
OA_lookup_df["la_name_x"].fillna(OA_lookup_df["la_name_y"], inplace=True)
OA_lookup_df["region_name_x"].fillna(OA_lookup_df["region_name_y"], inplace=True)
OA_lookup_df.drop(["ladcd", "ladnm", "la_code_y","la_name_y", "region_name_y"], axis=1, inplace=True)
OA_lookup_df.dropna(subset=["la_name_x"], inplace=True)
OA_lookup_df["pcd7"]=OA_lookup_df["pcd7"].str.replace(' ','')
OA_lookup_df.columns = ['PCD7', 'OA11CD', 'LSOA11CD', 'MSOA11CD', 'LAD11CD', 'Local Authority', 'Region']

if len(local_authority)>0:
    OA_lookup_df=OA_lookup_df.loc[OA_lookup_df['Local Authority'].isin(local_authority),:]

final_df = OA_lookup_df.loc[:, ["OA11CD", "LSOA11CD", "Local Authority"]].drop_duplicates()
final_df.head()

OA11CD   LSOA11CD Local Authority
34000  E00120196  E01023667       St Albans
34050  E00120186  E01023665       St Albans
34053  E00120265  E01023681       St Albans
34054  E00120198  E01023666       St Albans
34055  E00120188  E01023665       St Albans

### Add rurality information

In [446]:
rurality_file = "census_OA_data_England_and_Wales.xlsx"
rurality_df = pd.read_excel(path_input_data+os.path.sep+rurality_file)
rurality_df = rurality_df[["N_Households", "Rurality", 'OA_Code']]
rurality_df["Rurality"].replace({'Village': 'Village, Town and Fringe',
                              'Town and Fringe': 'Village, Town and Fringe'}, inplace=True)
rurality_columns= ["Rurality_"+str(x) for x in rurality_df["Rurality"].unique() if x is not np.nan]
rurality_df = pd.get_dummies(rurality_df, columns=["Rurality"])

rurality_df.head()

N_Households    OA_Code  Rurality_Hamlet & Isolated Dwellings  \
0           119  E00078837                                     0   
1           122  E00078838                                     0   
2            97  E00078839                                     0   
3            78  E00078840                                     1   
4           117  E00078841                                     0   

   Rurality_Urban >10K  Rurality_Village, Town and Fringe  
0                    0                                  1  
1                    0                                  1  
2                    0                                  1  
3                    0                                  0  
4                    0                                  1

In [447]:
final_df = pd.merge(rurality_df,final_df, left_on='OA_Code', right_on='OA11CD', how='right')
final_df = final_df.groupby('LSOA11CD').sum()
final_df["Rurality"] = final_df[rurality_columns].idxmax(axis=1)
final_df.drop(rurality_columns, axis=1, inplace=True)
LSOA_lookup_df = OA_lookup_df.loc[:,["LSOA11CD", "MSOA11CD", "LAD11CD", "Local Authority"]].drop_duplicates()
final_df = pd.merge(final_df,LSOA_lookup_df, left_index=True, right_on='LSOA11CD', how='left')
final_df.set_index("LSOA11CD", inplace=True, drop=True)
final_df.head()

N_Households             Rurality   MSOA11CD    LAD11CD  \
LSOA11CD                                                             
E01000001           876  Rurality_Urban >10K  E02000001  E09000001   
E01000002           830  Rurality_Urban >10K  E02000001  E09000001   
E01000003           817  Rurality_Urban >10K  E02000001  E09000001   
E01000005           467  Rurality_Urban >10K  E02000001  E09000001   
E01000006           543  Rurality_Urban >10K  E02000017  E09000002   

                Local Authority  
LSOA11CD                         
E01000001        City of London  
E01000002        City of London  
E01000003        City of London  
E01000005        City of London  
E01000006  Barking and Dagenham

### Add census data dwelling type by heating type

In [448]:
dwelling_heating_file = "CT0213.xls"

frame = []

dwelling_type = ["Detached", "Semi-detached", "Terraced", "Flat"]
heating_type = ["No central heating", "Gas boiler", 'Resistance heating', "Oil boiler", "Solid fuel boiler"]
count = 2

for dwelling in dwelling_type:
    df = pd.read_excel(path_input_data+os.path.sep+dwelling_heating_file, sheet_name=count, header=11, index_col=0)
    df.drop(df.columns[0], axis=1, inplace=True)
    df.drop(df.columns[5], axis=1, inplace=True)
    df.columns = [dwelling + " " +heating+ " 2011" for heating in heating_type] 
    df["Code"] = df.index.str.strip().str.split(' ').str.get(0)
    df.set_index("Code", inplace=True, drop=True)
    df.dropna(inplace=True)
    print(df.shape)
    count = count + 1
    frame.append(df)
dwelling_heating_df = pd.concat(frame, axis=1, sort=False)

(42314, 5)
(42314, 5)
(42314, 5)
(42314, 5)


In [449]:
final_df = pd.merge(final_df, dwelling_heating_df,left_index=True, right_index=True, how='left')
final_df.head()

N_Households             Rurality   MSOA11CD    LAD11CD  \
LSOA11CD                                                             
E01000001           876  Rurality_Urban >10K  E02000001  E09000001   
E01000002           830  Rurality_Urban >10K  E02000001  E09000001   
E01000003           817  Rurality_Urban >10K  E02000001  E09000001   
E01000005           467  Rurality_Urban >10K  E02000001  E09000001   
E01000006           543  Rurality_Urban >10K  E02000017  E09000002   

                Local Authority  Detached No central heating 2011  \
LSOA11CD                                                            
E01000001        City of London                               0.0   
E01000002        City of London                               0.0   
E01000003        City of London                               0.0   
E01000005        City of London                               0.0   
E01000006  Barking and Dagenham                               2.0   

           Detached Gas boiler 2011  Detached Resistance heating 2011  \
LSOA11CD                                                                
E01000001                       0.0                               0.0   
E01000002                       0.0                               0.0   
E01000003                       0.0                               0.0   
E01000005                       1.0                               0.0   
E01000006                      26.0                               1.0   

           Detached Oil boiler 2011  Detached Solid fuel boiler 2011  ...  \
LSOA11CD                                                              ...   
E01000001                       0.0                              0.0  ...   
E01000002                       0.0                              0.0  ...   
E01000003                       0.0                              0.0  ...   
E01000005                       0.0                              0.0  ...   
E01000006                       0.0                              0.0  ...   

           Terraced No central heating 2011  Terraced Gas boiler 2011  \
LSOA11CD                                                                
E01000001                               0.0                       1.0   
E01000002                               0.0                       3.0   
E01000003                               0.0                       2.0   
E01000005                               0.0                       0.0   
E01000006                               7.0                     263.0   

           Terraced Resistance heating 2011  Terraced Oil boiler 2011  \
LSOA11CD                                                                
E01000001                               8.0                       0.0   
E01000002                              23.0                       0.0   
E01000003                               0.0                       0.0   
E01000005                               0.0                       0.0   
E01000006                               7.0                       0.0   

           Terraced Solid fuel boiler 2011  Flat No central heating 2011  \
LSOA11CD                                                                   
E01000001                              0.0                          10.0   
E01000002                              0.0                          15.0   
E01000003                              0.0                          23.0   
E01000005                              0.0                           9.0   
E01000006                              1.0                          12.0   

           Flat Gas boiler 2011  Flat Resistance heating 2011  \
LSOA11CD                                                        
E01000001                  79.0                         564.0   
E01000002                  36.0                         515.0   
E01000003                 496.0                         209.0   
E01000005                 224.0                          98.0   
E01000006                  26.0      

### Add area to LSOA

In [450]:
file = 'UK_2011_LSOA_with_area.csv'

In [451]:
area_df = pd.read_csv(path_input_data+os.path.sep+file, index_col=1, dtype={"Area":float})
area_df["Area"] = area_df["Area"]/1000000
area_df.rename(columns = {'Area':'Area (km2)'}, inplace=True)
area_df.head()

OBJECTID                       AREA_NAME  MaxSimpTol  MinSimpTol  \
AREA_ID                                                                       
E01025921      1001  North West Leicestershire 006D          75        75.0   
E01023929      1002            Welwyn Hatfield 010A          75        75.0   
E01011976      1003                 Hartlepool 005D          75        75.0   
E01011977      1004                 Hartlepool 012C          75        75.0   
E01011974      1005                 Hartlepool 005B          75        37.5   

           OBJECTID_1 GeographyCode  KS601EW0001  KS601EW0002  KS601EW0003  \
AREA_ID                                                                      
E01025921     32810.0     E01025921       1151.0        170.0        473.0   
E01023929     30860.0     E01023929       1177.0        169.0        481.0   
E01011976     19182.0     E01011976        754.0        111.0        223.0   
E01011977     19183.0     E01011977       1266.0        209.0        343.0   
E01011974     19180.0     E01011974       1384.0        165.0        572.0   

           KS601EW0004  ...  KS601EW0011  KS601EW0012  KS601EW0013  \
AREA_ID                 ...                                          
E01025921         94.0  ...         13.0          3.0          5.0   
E01023929        110.0  ...         31.0         12.0         11.0   
E01011976         35.0  ...         23.0         21.0          6.0   
E01011977         53.0  ...         54.0         46.0         27.0   
E01011974         62.0  ...         40.0         30.0         28.0   

           KS601EW0014  KS601EW0015  Full_time_PC  Part_time_PC  \
AREA_ID                                                           
E01025921          0.0         10.0     41.094700     14.769765   
E01023929          4.0         18.0     40.866610     14.358539   
E01011976         27.0         35.0     29.575597     14.721485   
E01011977         31.0         61.0     27.093207     16.508689   
E01011974         24.0         49.0     41.329480     11.921965   

           Unemployed_PC  Retired_PC  Area (km2)  
AREA_ID                                           
E01025921       1.650738   21.894005    6.032557  
E01023929       3.313509   12.744265    0.313431  
E01011976      12.466844   11.671088    0.118284  
E01011977      11.769352   10.110585    0.347408  
E01011974       8.670520    9.176301    0.857310  

[5 rows x 26 columns]

In [452]:
final_df=pd.merge(final_df, area_df['Area (km2)'],left_index=True, right_index=True, how='left')
final_df['Area (km2)'].fillna(-1, inplace=True)
final_df.head()

N_Households             Rurality   MSOA11CD    LAD11CD  \
LSOA11CD                                                             
E01000001           876  Rurality_Urban >10K  E02000001  E09000001   
E01000002           830  Rurality_Urban >10K  E02000001  E09000001   
E01000003           817  Rurality_Urban >10K  E02000001  E09000001   
E01000005           467  Rurality_Urban >10K  E02000001  E09000001   
E01000006           543  Rurality_Urban >10K  E02000017  E09000002   

                Local Authority  Detached No central heating 2011  \
LSOA11CD                                                            
E01000001        City of London                               0.0   
E01000002        City of London                               0.0   
E01000003        City of London                               0.0   
E01000005        City of London                               0.0   
E01000006  Barking and Dagenham                               2.0   

           Detached Gas boiler 2011  Detached Resistance heating 2011  \
LSOA11CD                                                                
E01000001                       0.0                               0.0   
E01000002                       0.0                               0.0   
E01000003                       0.0                               0.0   
E01000005                       1.0                               0.0   
E01000006                      26.0                               1.0   

           Detached Oil boiler 2011  Detached Solid fuel boiler 2011  ...  \
LSOA11CD                                                              ...   
E01000001                       0.0                              0.0  ...   
E01000002                       0.0                              0.0  ...   
E01000003                       0.0                              0.0  ...   
E01000005                       0.0                              0.0  ...   
E01000006                       0.0                              0.0  ...   

           Terraced Gas boiler 2011  Terraced Resistance heating 2011  \
LSOA11CD                                                                
E01000001                       1.0                               8.0   
E01000002                       3.0                              23.0   
E01000003                       2.0                               0.0   
E01000005                       0.0                               0.0   
E01000006                     263.0                               7.0   

           Terraced Oil boiler 2011  Terraced Solid fuel boiler 2011  \
LSOA11CD                                                               
E01000001                       0.0                              0.0   
E01000002                       0.0                              0.0   
E01000003                       0.0                              0.0   
E01000005                       0.0                              0.0   
E01000006                       0.0                              1.0   

           Flat No central heating 2011  Flat Gas boiler 2011  \
LSOA11CD                                                        
E01000001                          10.0                  79.0   
E01000002                          15.0                  36.0   
E01000003                          23.0                 496.0   
E01000005                           9.0                 224.0   
E01000006                          12.0                  26.0   

           Flat Resistance heating 2011  Flat Oil boiler 2011  \
LSOA11CD                                                        
E01000001                         564.0                  10.0   
E01000002                         515.0                   6.0   
E01000003                         209.0                   1.0   
E01000005                          98.0                  25.0   
E01000006                          88.0                   1.0   

           Flat Solid fuel boiler 2011  Area (km2)  
LS

### Add road length to LSOA

In [453]:
file = 'UK_2011_LSOA_with_road.csv'

In [454]:
road_df = pd.read_csv(path_input_data+os.path.sep+file, dtype={"Sum_Shape_":float})
road_df.rename(columns={'Sum_Shape_':'Road length (m)'}, inplace=True)
road_df = pd.merge(OA_lookup_df[["OA11CD","LSOA11CD"]].drop_duplicates(), road_df[["geo_code", "Road length (m)"]], left_on="OA11CD", right_on="geo_code", how="left")
road_df = road_df.groupby(["LSOA11CD"]).sum().reset_index()
road_df['Road length (m)'].fillna(-1, inplace=True)
road_df.head()

LSOA11CD  Road length (m)
0  E01000001      2298.204579
1  E01000002      3603.807979
2  E01000003       817.923939
3  E01000005      4079.738602
4  E01000006      2520.445518

In [455]:
final_df = pd.merge(final_df, road_df,left_index=True, right_on="LSOA11CD", how='left')
final_df.head()

N_Households             Rurality   MSOA11CD    LAD11CD  \
0           876  Rurality_Urban >10K  E02000001  E09000001   
1           830  Rurality_Urban >10K  E02000001  E09000001   
2           817  Rurality_Urban >10K  E02000001  E09000001   
3           467  Rurality_Urban >10K  E02000001  E09000001   
4           543  Rurality_Urban >10K  E02000017  E09000002   

        Local Authority  Detached No central heating 2011  \
0        City of London                               0.0   
1        City of London                               0.0   
2        City of London                               0.0   
3        City of London                               0.0   
4  Barking and Dagenham                               2.0   

   Detached Gas boiler 2011  Detached Resistance heating 2011  \
0                       0.0                               0.0   
1                       0.0                               0.0   
2                       0.0                               0.0   
3                       1.0                               0.0   
4                      26.0                               1.0   

   Detached Oil boiler 2011  Detached Solid fuel boiler 2011  ...  \
0                       0.0                              0.0  ...   
1                       0.0                              0.0  ...   
2                       0.0                              0.0  ...   
3                       0.0                              0.0  ...   
4                       0.0                              0.0  ...   

   Terraced Oil boiler 2011  Terraced Solid fuel boiler 2011  \
0                       0.0                              0.0   
1                       0.0                              0.0   
2                       0.0                              0.0   
3                       0.0                              0.0   
4                       0.0                              1.0   

   Flat No central heating 2011  Flat Gas boiler 2011  \
0                          10.0                  79.0   
1                          15.0                  36.0   
2                          23.0                 496.0   
3                           9.0                 224.0   
4                          12.0                  26.0   

   Flat Resistance heating 2011  Flat Oil boiler 2011  \
0                         564.0                  10.0   
1                         515.0                   6.0   
2                         209.0                   1.0   
3                          98.0                  25.0   
4                          88.0                   1.0   

   Flat Solid fuel boiler 2011  Area (km2)   LSOA11CD  Road length (m)  
0                          0.0    0.135740  E01000001      2298.204579  
1                          0.0    0.223720  E01000002      3603.807979  
2                          0.0    0.062016  E01000003       817.923939  
3                          0.0    0.187404  E01000005      4079.738602  
4                          0.0    0.135204  E01000006      2520.445518  

[5 rows x 28 columns]

### Add number of households in 2018

In [456]:
## Add data for 2018
frames = []

year_list=['2018']

for yr in year_list:
    temp_df = pd.read_csv(path_input_data+os.path.sep+"LSOA_domestic_"+str(yr)+".csv",na_values='-')
    cols_to_keep = ["Lower Layer Super Output Area (LSOA) Code" , "Total number of domestic electricity meters"]
    temp_df = temp_df.loc[:, cols_to_keep].copy()
    temp_df.columns = ["LSOA code "+yr, 
                        "Total number of domestic electricity meters "+yr, 
                       ]
    temp_df["LSOA code "+yr]=temp_df["LSOA code "+yr].str.strip()
    temp_df.set_index("LSOA code "+yr, inplace=True)
    final_df = pd.merge(final_df, temp_df,left_on="LSOA11CD", right_on="LSOA code "+yr, how='left')
    for col in temp_df.iloc[:,:].columns:
        final_df[col].fillna(0, inplace=True)

In [457]:
final_df.rename(columns={'N_Households':'N_Households 2011'}, inplace=True) #
print("Number of households in 2011: ", '{:,}'.format(final_df['N_Households 2011'].sum()))

# the number of electricity meters is a good proxy to estimate the number of households per LSOA in 2018
final_df['N_Households 2018'] = final_df['Total number of domestic electricity meters 2018'] 
print("Number of households in 2018: ", '{:,}'.format(final_df['N_Households 2018'].sum()))

Number of households in 2011:  23,361,222
Number of households in 2018:  25,553,711


In [458]:
heating_cols = [
                'Detached Gas boiler 2011' ,
                'Detached Resistance heating 2011' ,
                'Detached Oil boiler 2011' ,
                'Detached Solid fuel boiler 2011' ,
                'Semi-detached Gas boiler 2011' ,
                'Semi-detached Resistance heating 2011' ,
                'Semi-detached Oil boiler 2011' ,
                'Semi-detached Solid fuel boiler 2011' ,
                'Terraced Gas boiler 2011' ,
                'Terraced Resistance heating 2011' ,
                'Terraced Oil boiler 2011' ,
                'Terraced Solid fuel boiler 2011' ,
                'Flat Gas boiler 2011' ,
                'Flat Resistance heating 2011' ,
                'Flat Oil boiler 2011' ,
                'Flat Solid fuel boiler 2011' ]

In [459]:
for nb_install in heating_cols:
    print(nb_install)
    final_df[nb_install[:-5]+" 2018"] = round(final_df[nb_install]/final_df["N_Households 2011"]*final_df['N_Households 2018'], 0)

Detached Gas boiler 2011
Detached Resistance heating 2011
Detached Oil boiler 2011
Detached Solid fuel boiler 2011
Semi-detached Gas boiler 2011
Semi-detached Resistance heating 2011
Semi-detached Oil boiler 2011
Semi-detached Solid fuel boiler 2011
Terraced Gas boiler 2011
Terraced Resistance heating 2011
Terraced Oil boiler 2011
Terraced Solid fuel boiler 2011
Flat Gas boiler 2011
Flat Resistance heating 2011
Flat Oil boiler 2011
Flat Solid fuel boiler 2011


In [460]:
final_df.set_index("LSOA11CD", inplace=True)
final_df.head()

N_Households 2011             Rurality   MSOA11CD    LAD11CD  \
LSOA11CD                                                                  
E01000001                876  Rurality_Urban >10K  E02000001  E09000001   
E01000002                830  Rurality_Urban >10K  E02000001  E09000001   
E01000003                817  Rurality_Urban >10K  E02000001  E09000001   
E01000005                467  Rurality_Urban >10K  E02000001  E09000001   
E01000006                543  Rurality_Urban >10K  E02000017  E09000002   

                Local Authority  Detached No central heating 2011  \
LSOA11CD                                                            
E01000001        City of London                               0.0   
E01000002        City of London                               0.0   
E01000003        City of London                               0.0   
E01000005        City of London                               0.0   
E01000006  Barking and Dagenham                               2.0   

           Detached Gas boiler 2011  Detached Resistance heating 2011  \
LSOA11CD                                                                
E01000001                       0.0                               0.0   
E01000002                       0.0                               0.0   
E01000003                       0.0                               0.0   
E01000005                       1.0                               0.0   
E01000006                      26.0                               1.0   

           Detached Oil boiler 2011  Detached Solid fuel boiler 2011  ...  \
LSOA11CD                                                              ...   
E01000001                       0.0                              0.0  ...   
E01000002                       0.0                              0.0  ...   
E01000003                       0.0                              0.0  ...   
E01000005                       0.0                              0.0  ...   
E01000006                       0.0                              0.0  ...   

           Semi-detached Oil boiler 2018  \
LSOA11CD                                   
E01000001                            0.0   
E01000002                            0.0   
E01000003                            0.0   
E01000005                            0.0   
E01000006                            0.0   

           Semi-detached Solid fuel boiler 2018  Terraced Gas boiler 2018  \
LSOA11CD                                                                    
E01000001                                   0.0                       1.0   
E01000002                                   0.0                       4.0   
E01000003                                   0.0                       3.0   
E01000005                                   0.0                       0.0   
E01000006                                   0.0                     256.0   

           Terraced Resistance heating 2018  Terraced Oil boiler 2018  \
LSOA11CD                                                                
E01000001                              10.0                       0.0   
E01000002                              32.0                       0.0   
E01000003                               0.0                       0.0   
E01000005                               0.0                       0.0   
E01000006                               7.0                       0.0   

           Terraced Solid fuel boiler 2018  Flat Gas boiler 2018  \
LSOA11CD                                                           
E01000001                              0.0                  95.0   
E01000002                              0.0                  50.0   
E01000003                              0.0                 718.0   
E01000005                              0.0                 270.0   
E01000006                              1.0                  25.0   

           Flat Resistance heating 2018  Flat Oil boiler 2018  \
LSOA11CD                                      

## EPC data
information regarding each field is described in : https://epc.opendatacommunities.org/docs/guidance#technical_notes

In [461]:
def mergeColumn(df, target, suffixes=["_x", "_y"]):
    list_col = df.columns
    org_col = target+suffixes[0]
    repl_col = target+suffixes[1]
    boolean=False
    if org_col in list_col:
        df[target] = df[org_col].fillna(df[repl_col])
        df.drop([org_col, repl_col], axis=1, inplace=True)
        boolean=True
    return boolean  

def getEPC(path, file):
    file = 'certificates.csv'
    df = pd.read_csv(path+os.path.sep+file)
    df["POSTCODE"] = df["POSTCODE"].str.replace(' ','')
    df=pd.merge(df, OA_lookup_df.loc[:,["PCD7", "LSOA11CD", "MSOA11CD", "LAD11CD"]],left_on="POSTCODE", right_on="PCD7", how='left')

    df.drop(["PCD7"], axis=1, inplace=True)
    df.replace('Bungalow', 'House', regex=True, inplace=True)
    df.replace('Maisonette', 'Flat', regex=True, inplace=True)
    df["Heat consumption (kWh)"]=0
    df["Space constrained ratio"]=0
    df["Heat_rating_changes [%]"]=0
    df["Heat_efficiency_changes [%]"]=0
    print(df.shape)
    return df

    
def setFlag(df):
    #Remove rows without a valid LSOA, MSOA or LA
    df["FLAG LSOA"] = df["LSOA11CD"].astype(str).str.len()==9
    df.drop(df[df["FLAG LSOA"]==False].index, inplace=True)

    df["FLAG MSOA"] = df["MSOA11CD"].astype(str).str.len()==9
    df.drop(df[df["FLAG MSOA"]==False].index, inplace=True)

    df["FLAG LA"] = df["LAD11CD"].astype(str).str.len()==9
    df.drop(df[df["FLAG LA"]==False].index, inplace=True)
    
    return df

def costTokWh(df):
    print("list of fuels: ", df["MAIN_FUEL"].unique()) 
    if potential:
        cost_column = "HEATING_COST_POTENTIAL"
    else:
        cost_column = "HEATING_COST_CURRENT" 
    #USING SAP price from january 2016: https://www.bre.co.uk/filelibrary/SAP/2012/RdSAP-fuel-prices-from-January-2018.xlsx
    price_of_elec = 15.32/100 #df_fuels.loc["Electricity", "Cost [GBP/kWh]"]
    price_of_gas = 4.32/100 #df_fuels.loc["Ngas", "Cost [GBP/kWh]"] 
    price_of_oil = 5.06/100 #df_fuels.loc["Oil", "Cost [GBP/kWh]"] 
    price_of_solid_fuel = 5.67/100 #df_fuels.loc["Biomass", "Cost [GBP/kWh]"] 

    #Efficiency from "combined"  individual_tech database
    eff_elec = 1
    eff_gas = 0.84
    eff_oil = 0.84
    eff_solid_fuel = 0.82
    eff_hp = 3.4
    
    df["Heat system"] = None
    df["MAINHEAT_DESCRIPTION"].fillna("No value", inplace=True)
    df["Heat consumption (kWh)"].dropna(inplace=True)
    
    gas_list = ["mains gas (not community)",
                #'mains gas - this is for backwards compatibility only and should not be used'
                ]
    
    df.loc[df["MAIN_FUEL"].isin(gas_list), "Heat consumption (kWh)"] = df.loc[df["MAIN_FUEL"].isin(gas_list), cost_column]/price_of_gas*eff_gas
    df.loc[df["MAIN_FUEL"].isin(gas_list), "Heat system"] = "Gas boiler"

    electricity_list = ["electricity (not community)", 'electricity - this is for backwards compatibility only and should not be used',
                       'Electricity: electricity, unspecified tariff']
    
    df.loc[df["MAIN_FUEL"].isin(electricity_list), "Heat system"]='Resistance heating'
    df.loc[df["MAINHEAT_DESCRIPTION"].str.contains("heat pump"),"Heat system"]="Heat pump"
    
    df.loc[df["Heat system"]=='Resistance heating', "Heat consumption (kWh)"] = df.loc[df["Heat system"]=='Resistance heating', cost_column]/price_of_elec*eff_elec
    df.loc[df["Heat system"]=="Heat pump", "Heat consumption (kWh)"] = df.loc[df["Heat system"]=="Heat pump", cost_column]/price_of_elec*eff_hp

    oil_list = ['appliances able to use mineral oil or liquid biofuel','oil (not community)', 'oil - this is for backwards compatibility only and should not be used']
    
    df.loc[df["MAIN_FUEL"].isin(oil_list), "Heat system"] = "Oil boiler"
    df.loc[df["Heat system"]=="Oil boiler", "Heat consumption (kWh)"] = df.loc[df["Heat system"]=="Oil boiler", cost_column]/price_of_oil*eff_oil

    solid_fuels = ['anthracite', 'house coal (not community)','wood logs', 'smokeless coal', 'house coal - this is for backwards compatibility only and should not be used',
                  'bulk wood pellets', 'wood chips']

    df.loc[df["MAIN_FUEL"].isin(solid_fuels), "Heat system"]="Solid fuel boiler"
    df.loc[df["Heat system"]=="Solid fuel boiler", "Heat consumption (kWh)"] = df.loc[df["Heat system"]=="Solid fuel boiler", cost_column]/price_of_solid_fuel*eff_solid_fuel
    return df

def threshold(df):
    # Remove inaccurate value from the dataset. e.g. everything under 25 kWh/m2
    min_kWh_m2 = 15 # minimum intensity Passive House (Passivhaus) standard is at 15 kWh/m2
    max_kWh_m2 = 400 
    max_m2 = 1000
    min_number_room = 1
    
    df["Heat per floor area (kWh/m2)"]=df["Heat consumption (kWh)"]/df["TOTAL_FLOOR_AREA"]
    print(df.loc[(df["Heat per floor area (kWh/m2)"]<min_kWh_m2),:].shape)
    df.fillna(0, inplace=True)
    to_drop = df.loc[(df["Heat per floor area (kWh/m2)"]<min_kWh_m2),:].index
    df.drop(to_drop, inplace=True)
    print(df.loc[(df["Heat per floor area (kWh/m2)"]>max_kWh_m2),:].shape)
    to_drop = df.loc[(df["Heat per floor area (kWh/m2)"]>max_kWh_m2),:].index
    df.drop(to_drop, inplace=True)
       
    
    # Used to assess the sapce availability to change heating system 
    # Source: Element Energy, “Analysis on abating direct emissions from ‘hard-to-decarbonise’ homes, with a view to informing the UK’s long term targets,” 2019.
    df["Space constrained ratio"] = df["TOTAL_FLOOR_AREA"]/df["NUMBER_HEATED_ROOMS"]
    df.loc[df["Space constrained ratio"]<=16, "Space constrained ratio"]=1
    df.loc[df["Space constrained ratio"]>16, "Space constrained ratio"]=0
    
    # Change in EPC and impact on heat
    to_drop = df.loc[df["POTENTIAL_ENERGY_EFFICIENCY"]<df["CURRENT_ENERGY_EFFICIENCY"], :].index
    df.drop(to_drop, inplace=True)
    
    to_drop = df.loc[df["HEATING_COST_CURRENT"]<df["HEATING_COST_POTENTIAL"]*(1+0.1), :].index
    df.drop(to_drop, inplace=True)
    
    df["Heat_rating_changes [%]"] = (df["HEATING_COST_POTENTIAL"] - df["HEATING_COST_CURRENT"])/df["HEATING_COST_CURRENT"]
    df["Heat_efficiency_changes [%]"] = (df["HEATING_COST_POTENTIAL"] - df["HEATING_COST_CURRENT"])/df["HEATING_COST_CURRENT"]/(df["POTENTIAL_ENERGY_EFFICIENCY"] - df["CURRENT_ENERGY_EFFICIENCY"])

    df["Heat_rating_changes [%]"].replace([np.inf, -np.inf], 0, inplace=True)
    df["Heat_efficiency_changes [%]"].replace([np.inf, -np.inf], 0, inplace=True)
    #Remove houses with less than 1 heated room
    to_drop = df.loc[(df["NUMBER_HEATED_ROOMS"]<min_number_room),:].index
    df.drop(to_drop, inplace=True)
    
    return df


def removeDuplicates(df):
    # Keep only the most uptodate EPC
    
    df = df.sort_values(["BUILDING_REFERENCE_NUMBER", "INSPECTION_DATE"])
    df.drop_duplicates(["BUILDING_REFERENCE_NUMBER"], keep="last", inplace=True)
    
    return df

def dwellingType(df):
    
    df["Dwelling type"]=None
    df.loc[df["PROPERTY_TYPE"]=="Flat", "Dwelling type"]="Flat"
    df.loc[df["PROPERTY_TYPE"]=="House", "Dwelling type"]=df.loc[df["PROPERTY_TYPE"]=="House", "BUILT_FORM"]
    list_dwelling_type = list(df["Dwelling type"].unique())
    list_dwelling_type = list(filter(None.__ne__, list_dwelling_type)) # Remove None from the list
    # temp_df.replace({dwel:"Terrace" for dwel in list_dwelling_type if "Terrace" in dwel}, regex=True, inplace=True)
   
    to_replace = {dwel:"Terraced" for dwel in list_dwelling_type if "Terrace" in dwel}
    df.replace(to_replace, inplace=True)
    df.replace("Semi-Detached", "Semi-detached", inplace=True)
    list_dwelling_type = list(df["Dwelling type"].unique())
    print(list_dwelling_type)
    
    to_drop = df.loc[(df["Dwelling type"]=='NO DATA!'),:].index
    df.drop(to_drop, inplace=True)
    
    df["Key"] = df["Dwelling type"].str.lower()+" "+df["Heat system"].str.lower()
    df["Key_EPC"] = df["CURRENT_ENERGY_RATING"]+" to "+df["POTENTIAL_ENERGY_RATING"]
    df.dropna(subset=['Key'], inplace=True)
    print("Shape:", df.shape)
    
    
    return df

def skeleton(LSOA_lookup):
    LSOA_lookup = LSOA_lookup.iloc[:,0:4] # use only the four first columns
    index = list(map(list, zip(*LSOA_lookup.values)))
    index = pd.MultiIndex.from_arrays(index, names=LSOA_lookup.columns)

    heating_type = ["Gas boiler", 'Resistance heating', "Oil boiler", "Solid fuel boiler", "Heat pump"]
    list_col = ["Mean "+x.lower()+" "+y.lower() for x in dwelling_type for y in heating_type]
    list_col.extend(["Average floor area of "+x.lower()+" "+y.lower() for x in dwelling_type for y in heating_type])
    list_col.extend(["Average number of rooms of "+x.lower()+" "+y.lower() for x in dwelling_type for y in heating_type])
    list_col.extend(["Average space constrained "+x.lower()+" "+y.lower() for x in dwelling_type for y in heating_type])
    EPC_ratings = ["A", "B", "C", "D", "E", "F", "G"]
    EPC_rating_cols = []
    EPC_eff_cols = []
    for ii, val in enumerate(EPC_ratings):
        for val2 in EPC_ratings[ii:]:
            EPC_rating_cols.append("EPC rating "+val2+" to "+val)
            EPC_eff_cols.append("EPC efficiency "+val2+" to "+val)
    list_col.extend(EPC_rating_cols)
    list_col.extend(EPC_eff_cols)
    LSOA_LA_df = pd.DataFrame(index=index, columns=list_col)
    LSOA_LA_df.reset_index(3,drop=True, inplace=True)
    LSOA_LA_df = LSOA_LA_df.reorder_levels(["LAD11CD",  'MSOA11CD','LSOA11CD'])
    return LSOA_LA_df


def populatingSkeleton(df, skeleton, target):
    list_col = list(skeleton.columns)
    key = "Key"
    if target=="Heat consumption (kWh)":
        list_col = [x for x in list_col if "Mean" in x]
        prefix = "Mean"
    elif target=="NUMBER_HEATED_ROOMS":
        list_col = [x for x in list_col if "rooms" in x]
        prefix = "Average number of rooms of"
    elif target=="TOTAL_FLOOR_AREA":
        list_col = [x for x in list_col if "floor" in x]
        prefix = "Average floor area of"
    elif target=="Space constrained ratio":
        list_col = [x for x in list_col if "space constrained" in x]
        prefix = "Average space constrained"
    elif target=="Heat_rating_changes [%]":
        
        list_col = [x for x in list_col if "EPC rating" in x]
        prefix = "EPC rating"
        key= "Key_EPC"
    elif target=="Heat_efficiency_changes [%]":
        list_col = [x for x in list_col if "EPC efficiency" in x]
        prefix = "EPC efficiency"
        key= "Key_EPC"
        
    print(list_col, prefix)
    df[key] = [prefix+" "+x for x in df[key].values]
    print(df[key].unique())
    
    df = df.loc[df[key].isin(list_col), :].copy()
    # Add the value available at LSOA level
    LSOA_df_count = df.groupby(["LAD11CD", "MSOA11CD", "LSOA11CD", key]).count()[target]
    LSOA_df_count[LSOA_df_count<4]=np.nan #Remove the archetypes with too few properties
    LSOA_df = df.groupby(["LAD11CD", "MSOA11CD", "LSOA11CD", key]).sum()[target]
    LSOA_df = LSOA_df/LSOA_df_count
    LSOA_df = LSOA_df.to_frame()
    LSOA_df = LSOA_df.unstack(3)
    LSOA_df.columns = LSOA_df.columns.droplevel(0)
    
    populated_skeleton = pd.merge(skeleton, LSOA_df, left_index=True, right_index=True, how='left')
    for col in list_col:
        mergeColumn(populated_skeleton, col)
    populated_skeleton.reset_index(level=2, inplace=True)
    
    # Add the value available at MSOA level
    MSOA_df_count = df.groupby(["LAD11CD", "MSOA11CD", key]).count()[target]
    MSOA_df_count[MSOA_df_count<4]=np.nan #Remove the archetypes with too few properties
    MSOA_df = df.groupby(["LAD11CD", "MSOA11CD", key]).sum()[target]
    MSOA_df = MSOA_df/MSOA_df_count
    MSOA_df = MSOA_df.to_frame()
    MSOA_df = MSOA_df.unstack(2)
    MSOA_df.columns = MSOA_df.columns.droplevel(0)

    populated_skeleton = pd.merge(populated_skeleton, MSOA_df, left_index=True, right_index=True, how='left')
    for col in list_col:
        mergeColumn(populated_skeleton, col)
        
    populated_skeleton.reset_index(level=1, inplace=True)
    
    # Add the value available at LA level
    LA_df_count = df.groupby(["LAD11CD", key]).count()[target]
    LA_df_count[LA_df_count<4]=np.nan #Remove the archetypes with too few properties
    LA_df = df.groupby(["LAD11CD", key]).sum()[target]
    LA_df = LA_df/LA_df_count
    LA_df = LA_df.to_frame()
    LA_df = LA_df.unstack(1)
    LA_df.columns = LA_df.columns.droplevel(0)
    LA_df.fillna(LA_df.mean() ,inplace=True)
    
    populated_skeleton = pd.merge(populated_skeleton, LA_df, left_index=True, right_index=True, how='left')
    for col in list_col:
        mergeColumn(populated_skeleton, col)
        
    populated_skeleton.reset_index(inplace=True)
    populated_skeleton.set_index(["LAD11CD", "MSOA11CD", "LSOA11CD"], inplace=True, drop=True)
    
    #populated_skeleton["Mean flat oil boiler"].fillna(populated_skeleton["Mean flat solid fuel boiler"], inplace=True)
    
    return populated_skeleton

def epcToLSOA(path, fn, LSOA_lookup):
    epc_df = getEPC(path, fn)
    org_EPC_number = len(epc_df)
    epc_df = setFlag(epc_df)
    epc_df = costTokWh(epc_df)
    epc_df = threshold(epc_df)
    epc_df = dwellingType(epc_df)
    epc_df = removeDuplicates(epc_df)
    final_EPC_number = len(epc_df)
    skeleton_df = skeleton(LSOA_lookup)
    df = populatingSkeleton(epc_df.copy(), skeleton_df, "Heat consumption (kWh)")
    df = populatingSkeleton(epc_df.copy(), df, "NUMBER_HEATED_ROOMS")
    df = populatingSkeleton(epc_df.copy(), df, "TOTAL_FLOOR_AREA")
    df = populatingSkeleton(epc_df.copy(), df, "Space constrained ratio")
    df = populatingSkeleton(epc_df.copy(), df, "Heat_rating_changes [%]")
    df = populatingSkeleton(epc_df.copy(), df, "Heat_efficiency_changes [%]")
    df.reset_index(inplace=True)
    df.set_index("LSOA11CD", inplace=True)
    df.drop(["MSOA11CD", "LAD11CD"], axis=1, inplace=True)

    return df, org_EPC_number, final_EPC_number

In [463]:
# uniformisation of the string values

list_LA = OA_lookup_df["Local Authority"].unique()
list_LA = [x.replace(' ', '') for x in list_LA]
list_LA = [x.replace('-', '') for x in list_LA]
list_LA = [x.replace("'", '') for x in list_LA]
list_LA = [x.replace(".", '') for x in list_LA]

LSOA_lookup_df["Local Authority nospace"] = LSOA_lookup_df["Local Authority"].str.replace('-','')
LSOA_lookup_df["Local Authority nospace"] = LSOA_lookup_df["Local Authority nospace"].str.replace(".",'')
LSOA_lookup_df["Local Authority nospace"] = LSOA_lookup_df["Local Authority nospace"].str.replace("'",'')
LSOA_lookup_df["Local Authority nospace"] = LSOA_lookup_df["Local Authority nospace"].str.replace(' ','')

C:\Users\sceac10\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:10: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will*not* be treated as literal strings when regex=True.
  # Remove the CWD from sys.path while we load stuff.


In [464]:
number_epc_df = pd.DataFrame(columns = ["Original number", "Final number"])

# output_df.set_index("LSOA11CD", inplace=True)
for fn in os.listdir(path_EPCs):
    LA_name = fn.split('-')[2:]
    LA_name = ''.join(LA_name)
    print(LA_name)
    if LA_name in list_LA:
        LSOA_lookup = LSOA_lookup_df.loc[LSOA_lookup_df["Local Authority nospace"]==LA_name, :]
        if LSOA_lookup.shape[0]>0:
            temp_df, org_number, final_number = epcToLSOA(path_EPCs+os.path.sep+fn+os.path.sep, file, LSOA_lookup)
            number_epc_df.loc[LA_name] = [org_number, final_number]
            final_df = pd.merge(final_df, temp_df, left_index=True, right_index=True, how='left')
            for col in temp_df.columns:
                mergeColumn(final_df, col)
        else: print("ERROR WITH NAME !!!!!!!!!!!!!!!!!!!", LA_name)
    else:
        print("Out", LA_name, fn)

Hartlepool
(30681, 92)
list of fuels:  ['mains gas - this is for backwards compatibility only and should not be used'
 'mains gas (not community)' 'NO DATA!'
 'electricity - this is for backwards compatibility only and should not be used'
 'electricity (not community)'
 'To be used only when there is no heating/hot-water system'
 'Electricity: electricity, unspecified tariff' 'mains gas (community)'
 'INVALID!' 'oil (not community)' 'dual fuel - mineral + wood'
 'LPG - this is for backwards compatibility only and should not be used'
 'oil - this is for backwards compatibility only and should not be used'
 'smokeless coal' 'LPG (not community)' 'B30D (community)'
 'house coal (not community)' 'bulk wood pellets'
 'house coal - this is for backwards compatibility only and should not be used'
 'biomass (community)' 'wood logs' 'bottled LPG']
(10620, 97)
(5, 97)
['Terraced', 'Semi-detached', 'Detached', 'Flat', None]
Shape: (14861, 100)
['Mean detached gas boiler', 'Mean detached resistanc

['EPC rating A to A', 'EPC rating B to A', 'EPC rating C to A', 'EPC rating D to A', 'EPC rating E to A', 'EPC rating F to A', 'EPC rating G to A', 'EPC rating B to B', 'EPC rating C to B', 'EPC rating D to B', 'EPC rating E to B', 'EPC rating F to B', 'EPC rating G to B', 'EPC rating C to C', 'EPC rating D to C', 'EPC rating E to C', 'EPC rating F to C', 'EPC rating G to C', 'EPC rating D to D', 'EPC rating E to D', 'EPC rating F to D', 'EPC rating G to D', 'EPC rating E to E', 'EPC rating F to E', 'EPC rating G to E', 'EPC rating F to F', 'EPC rating G to F', 'EPC rating G to G'] EPC rating
['EPC rating D to C' 'EPC rating E to D' 'EPC rating E to C'
 'EPC rating D to B' 'EPC rating F to C' 'EPC rating D to D'
 'EPC rating C to B' 'EPC rating G to C' 'EPC rating C to C'
 'EPC rating F to B' 'EPC rating E to B' 'EPC rating D to A'
 'EPC rating B to B' 'EPC rating F to D' 'EPC rating G to G'
 'EPC rating E to A' 'EPC rating F to E' 'EPC rating B to A'
 'EPC rating C to A' 'EPC rating G

['Average space constrained detached gas boiler', 'Average space constrained detached resistance heating', 'Average space constrained detached oil boiler', 'Average space constrained detached solid fuel boiler', 'Average space constrained detached heat pump', 'Average space constrained semi-detached gas boiler', 'Average space constrained semi-detached resistance heating', 'Average space constrained semi-detached oil boiler', 'Average space constrained semi-detached solid fuel boiler', 'Average space constrained semi-detached heat pump', 'Average space constrained terraced gas boiler', 'Average space constrained terraced resistance heating', 'Average space constrained terraced oil boiler', 'Average space constrained terraced solid fuel boiler', 'Average space constrained terraced heat pump', 'Average space constrained flat gas boiler', 'Average space constrained flat resistance heating', 'Average space constrained flat oil boiler', 'Average space constrained flat solid fuel boiler', 'A

['Average floor area of detached gas boiler', 'Average floor area of detached resistance heating', 'Average floor area of detached oil boiler', 'Average floor area of detached solid fuel boiler', 'Average floor area of detached heat pump', 'Average floor area of semi-detached gas boiler', 'Average floor area of semi-detached resistance heating', 'Average floor area of semi-detached oil boiler', 'Average floor area of semi-detached solid fuel boiler', 'Average floor area of semi-detached heat pump', 'Average floor area of terraced gas boiler', 'Average floor area of terraced resistance heating', 'Average floor area of terraced oil boiler', 'Average floor area of terraced solid fuel boiler', 'Average floor area of terraced heat pump', 'Average floor area of flat gas boiler', 'Average floor area of flat resistance heating', 'Average floor area of flat oil boiler', 'Average floor area of flat solid fuel boiler', 'Average floor area of flat heat pump'] Average floor area of
['Average floor 

['Average number of rooms of detached gas boiler', 'Average number of rooms of detached resistance heating', 'Average number of rooms of detached oil boiler', 'Average number of rooms of detached solid fuel boiler', 'Average number of rooms of detached heat pump', 'Average number of rooms of semi-detached gas boiler', 'Average number of rooms of semi-detached resistance heating', 'Average number of rooms of semi-detached oil boiler', 'Average number of rooms of semi-detached solid fuel boiler', 'Average number of rooms of semi-detached heat pump', 'Average number of rooms of terraced gas boiler', 'Average number of rooms of terraced resistance heating', 'Average number of rooms of terraced oil boiler', 'Average number of rooms of terraced solid fuel boiler', 'Average number of rooms of terraced heat pump', 'Average number of rooms of flat gas boiler', 'Average number of rooms of flat resistance heating', 'Average number of rooms of flat oil boiler', 'Average number of rooms of flat sol

...

['Average space constrained detached gas boiler', 'Average space constrained detached resistance heating', 'Average space constrained detached oil boiler', 'Average space constrained detached solid fuel boiler', 'Average space constrained detached heat pump', 'Average space constrained semi-detached gas boiler', 'Average space constrained semi-detached resistance heating', 'Average space constrained semi-detached oil boiler', 'Average space constrained semi-detached solid fuel boiler', 'Average space constrained semi-detached heat pump', 'Average space constrained terraced gas boiler', 'Average space constrained terraced resistance heating', 'Average space constrained terraced oil boiler', 'Average space constrained terraced solid fuel boiler', 'Average space constrained terraced heat pump', 'Average space constrained flat gas boiler', 'Average space constrained flat resistance heating', 'Average space constrained flat oil boiler', 'Average space constrained flat solid fuel boiler', 'A

['Average floor area of detached gas boiler', 'Average floor area of detached resistance heating', 'Average floor area of detached oil boiler', 'Average floor area of detached solid fuel boiler', 'Average floor area of detached heat pump', 'Average floor area of semi-detached gas boiler', 'Average floor area of semi-detached resistance heating', 'Average floor area of semi-detached oil boiler', 'Average floor area of semi-detached solid fuel boiler', 'Average floor area of semi-detached heat pump', 'Average floor area of terraced gas boiler', 'Average floor area of terraced resistance heating', 'Average floor area of terraced oil boiler', 'Average floor area of terraced solid fuel boiler', 'Average floor area of terraced heat pump', 'Average floor area of flat gas boiler', 'Average floor area of flat resistance heating', 'Average floor area of flat oil boiler', 'Average floor area of flat solid fuel boiler', 'Average floor area of flat heat pump'] Average floor area of
['Average floor 

['Average number of rooms of detached gas boiler', 'Average number of rooms of detached resistance heating', 'Average number of rooms of detached oil boiler', 'Average number of rooms of detached solid fuel boiler', 'Average number of rooms of detached heat pump', 'Average number of rooms of semi-detached gas boiler', 'Average number of rooms of semi-detached resistance heating', 'Average number of rooms of semi-detached oil boiler', 'Average number of rooms of semi-detached solid fuel boiler', 'Average number of rooms of semi-detached heat pump', 'Average number of rooms of terraced gas boiler', 'Average number of rooms of terraced resistance heating', 'Average number of rooms of terraced oil boiler', 'Average number of rooms of terraced solid fuel boiler', 'Average number of rooms of terraced heat pump', 'Average number of rooms of flat gas boiler', 'Average number of rooms of flat resistance heating', 'Average number of rooms of flat oil boiler', 'Average number of rooms of flat sol

MerthyrTydfil
(17891, 92)
list of fuels:  ['mains gas - this is for backwards compatibility only and should not be used'
 'mains gas (not community)'
 'LPG - this is for backwards compatibility only and should not be used'
 'INVALID!' 'To be used only when there is no heating/hot-water system'
 'smokeless coal'
 'house coal - this is for backwards compatibility only and should not be used'
 'electricity - this is for backwards compatibility only and should not be used'
 'mains gas (community)' 'NO DATA!'
 'oil - this is for backwards compatibility only and should not be used'
 'electricity (not community)' 'house coal (not community)'
 'oil (not community)' 'LPG (not community)' 'electricity (community)'
 'dual fuel - mineral + wood' 'wood logs' 'bottled LPG' 'anthracite'
 'Electricity: electricity, unspecified tariff' 'bulk wood pellets'
 'B30K (not community)']
(9192, 97)
(6, 97)
['Semi-detached', 'Terraced', 'Detached', 'Flat']
Shape: (6934, 100)
['Mean detached gas boiler', 'Mean d

['EPC efficiency A to A', 'EPC efficiency B to A', 'EPC efficiency C to A', 'EPC efficiency D to A', 'EPC efficiency E to A', 'EPC efficiency F to A', 'EPC efficiency G to A', 'EPC efficiency B to B', 'EPC efficiency C to B', 'EPC efficiency D to B', 'EPC efficiency E to B', 'EPC efficiency F to B', 'EPC efficiency G to B', 'EPC efficiency C to C', 'EPC efficiency D to C', 'EPC efficiency E to C', 'EPC efficiency F to C', 'EPC efficiency G to C', 'EPC efficiency D to D', 'EPC efficiency E to D', 'EPC efficiency F to D', 'EPC efficiency G to D', 'EPC efficiency E to E', 'EPC efficiency F to E', 'EPC efficiency G to E', 'EPC efficiency F to F', 'EPC efficiency G to F', 'EPC efficiency G to G'] EPC efficiency
['EPC efficiency E to B' 'EPC efficiency D to C' 'EPC efficiency E to C'
 'EPC efficiency D to B' 'EPC efficiency F to B' 'EPC efficiency D to D'
 'EPC efficiency C to B' 'EPC efficiency C to A' 'EPC efficiency G to F'
 'EPC efficiency F to C' 'EPC efficiency F to E' 'EPC efficiency 

In [465]:
number_epc_df.sum()

Original number    15616549
Final number        6081764
dtype: object

In [429]:
potential

False

In [466]:
cols = ['Flat Heat pump', 'Detached Gas boiler', 'Detached Resistance heating', 'Detached Oil boiler', 'Detached Solid fuel boiler',
 'Detached Heat pump', 'Semi-detached Gas boiler', 'Semi-detached Resistance heating', 'Semi-detached Oil boiler',
 'Semi-detached Solid fuel boiler', 'Semi-detached Heat pump', 'Terraced Gas boiler', 'Terraced Resistance heating',
 'Terraced Oil boiler', 'Terraced Solid fuel boiler', 'Terraced Heat pump', 'Flat Gas boiler', 'Flat Resistance heating', 'Flat Oil boiler',
 'Flat Solid fuel boiler']

for p in ["Mean","Average number of rooms of", "Average floor area of", "Average space constrained"]:
    dict_avg_demand = {}
    temp_cols = [p+" "+x.lower() for x in cols]
    for col in temp_cols:
        dict_avg_demand[col]=final_df[col].mean()
    print(dict_avg_demand)

{'Mean flat heat pump': 5839.768497366066, 'Mean detached gas boiler': 14589.644077982724, 'Mean detached resistance heating': 5550.939151840999, 'Mean detached oil boiler': 20442.887090034532, 'Mean detached solid fuel boiler': 13221.200322729735, 'Mean detached heat pump': 27478.618425106422, 'Mean semi-detached gas boiler': 11176.994056933589, 'Mean semi-detached resistance heating': 3812.4039727079357, 'Mean semi-detached oil boiler': 13178.966362117755, 'Mean semi-detached solid fuel boiler': 8384.13646738717, 'Mean semi-detached heat pump': 13397.401257373627, 'Mean terraced gas boiler': 9808.588429358784, 'Mean terraced resistance heating': 3251.5967760104672, 'Mean terraced oil boiler': 11664.662458327663, 'Mean terraced solid fuel boiler': 7475.750706061542, 'Mean terraced heat pump': 10588.61787728848, 'Mean flat gas boiler': 6683.579422146057, 'Mean flat resistance heating': 1988.1744399227346, 'Mean flat oil boiler': 8115.289346063978, 'Mean flat solid fuel boiler': 5002.95

In [467]:
if potential: #average value in England and Wales after considering EE measures (obtained from a previous run)
    avg_heat_demand ={'Mean flat heat pump': 5839.768497366066,
                      'Mean detached gas boiler': 14589.644077982724,
                      'Mean detached resistance heating': 5550.939151840999,
                      'Mean detached oil boiler': 20442.887090034532,
                      'Mean detached solid fuel boiler': 13221.200322729735,
                      'Mean detached heat pump': 27478.618425106422,
                      'Mean semi-detached gas boiler': 11176.994056933589,
                      'Mean semi-detached resistance heating': 3812.4039727079357,
                      'Mean semi-detached oil boiler': 13178.966362117755, 
                      'Mean semi-detached solid fuel boiler': 8384.13646738717,
                      'Mean semi-detached heat pump': 13397.401257373627,
                      'Mean terraced gas boiler': 9808.588429358784,
                      'Mean terraced resistance heating': 3251.5967760104672,
                      'Mean terraced oil boiler': 11664.662458327663,
                      'Mean terraced solid fuel boiler': 7475.750706061542, 
                      'Mean terraced heat pump': 10588.61787728848, 
                      'Mean flat gas boiler': 6683.579422146057, 
                      'Mean flat resistance heating': 1988.1744399227346,
                      'Mean flat oil boiler': 8115.289346063978, 
                      'Mean flat solid fuel boiler': 5002.95209113117}
    
else: #average value in England and Wales before considering EE measures (obtained from a previous run)
    avg_heat_demand = {'Mean flat heat pump': 8317.654679323365,
                       'Mean detached gas boiler': 22255.992657350296, 
                       'Mean detached resistance heating': 10228.077961518446, 
                       'Mean detached oil boiler': 33141.41672297774, 
                       'Mean detached solid fuel boiler': 20875.19512086178, 
                       'Mean detached heat pump': 37840.82307995661, 
                       'Mean semi-detached gas boiler': 16912.665791856532, 
                       'Mean semi-detached resistance heating': 7003.306852855303,
                       'Mean semi-detached oil boiler': 21490.58787143911, 
                       'Mean semi-detached solid fuel boiler': 12979.552672499918,
                       'Mean semi-detached heat pump': 18264.7813841389, 
                       'Mean terraced gas boiler': 14512.460427801987, 
                       'Mean terraced resistance heating': 5780.188713745561, 
                       'Mean terraced oil boiler': 18130.40810398572, 
                       'Mean terraced solid fuel boiler': 11399.774271931581, 
                       'Mean terraced heat pump': 14145.681348359638, 
                       'Mean flat gas boiler': 9647.65715063135, 
                       'Mean flat resistance heating': 3273.160923480452, 
                       'Mean flat oil boiler': 12937.408383942113, 
                       'Mean flat solid fuel boiler': 7186.23811026301}
    

for key, value in avg_heat_demand.items():
    final_df[key].fillna(final_df[key].mean(), inplace=True)

In [468]:
# Remove dwellings with heat pumps
heatpump_cols = [c for c in final_df.columns if "Heat pump" in c]
final_df.drop(heatpump_cols, axis=1, inplace=True)

### Formatting of the name of the columns

In [469]:
current_categories = ['Detached Gas boiler' ,
                        'Detached Resistance heating' ,
                        'Detached Oil boiler' ,
                        'Detached Biomass boiler' ,
                        'Semi-detached Gas boiler' ,
                        'Semi-detached Resistance heating' ,
                        'Semi-detached Oil boiler' ,
                        'Semi-detached Biomass boiler' ,
                        'Terraced Gas boiler' ,
                        'Terraced Resistance heating' ,
                        'Terraced Oil boiler' ,
                        'Terraced Biomass boiler' ,
                        'Flat Gas boiler' ,
                        'Flat Resistance heating' ,
                        'Flat Oil boiler' ,
                        'Flat Biomass boiler' ]

In [505]:
final_df = pd.read_csv(saving_path+os.path.sep+"LSOAs_in_England_Wales_before_EE_heat_demand.csv", index_col=0)
potential = False
final_df

N_Households 2011             Rurality   MSOA11CD    LAD11CD  \
LSOA11CD                                                                  
E01000001                876  Rurality_Urban >10K  E02000001  E09000001   
E01000002                830  Rurality_Urban >10K  E02000001  E09000001   
E01000003                817  Rurality_Urban >10K  E02000001  E09000001   
E01000005                467  Rurality_Urban >10K  E02000001  E09000001   
E01000006                543  Rurality_Urban >10K  E02000017  E09000002   
...                      ...                  ...        ...        ...   
W01001954                637  Rurality_Urban >10K  W02000372  W06000015   
W01001955               1153  Rurality_Urban >10K  W02000192  W06000011   
W01001956                803  Rurality_Urban >10K  W02000190  W06000011   
W01001957                411  Rurality_Urban >10K  W02000192  W06000011   
W01001958                836  Rurality_Urban >10K  W02000192  W06000011   

                Local Authority  Detached No central heating 2011  \
LSOA11CD                                                            
E01000001        City of London                               0.0   
E01000002        City of London                               0.0   
E01000003        City of London                               0.0   
E01000005        City of London                               0.0   
E01000006  Barking and Dagenham                               2.0   
...                         ...                               ...   
W01001954               Cardiff                               0.0   
W01001955               Swansea                               0.0   
W01001956               Swansea                               1.0   
W01001957               Swansea                               0.0   
W01001958               Swansea                               0.0   

           Number of detached gas boiler in 2011  \
LSOA11CD                                           
E01000001                                    0.0   
E01000002                                    0.0   
E01000003                                    0.0   
E01000005                                    1.0   
E01000006                                   26.0   
...                                          ...   
W01001954                                  274.0   
W01001955                                   10.0   
W01001956                                  259.0   
W01001957                                    3.0   
W01001958                                    8.0   

           Number of detached resistance heating in 2011  \
LSOA11CD                                                   
E01000001                                            0.0   
E01000002                                            0.0   
E01000003                                            0.0   
E01000005                                            0.0   
E01000006                                            1.0   
...                                                  ...   
W01001954                                            0.0   
W01001955                                            6.0   
W01001956                                            3.0   
W01001957                                            1.0   
W01001958                                            0.0   

           Number of detached oil boiler in 2011  \
LSOA11CD                                           
E01000001                                    0.0   
E01000002                                    0.0   
E01000003                                    0.0   
E01000005                                    0.0   
E01000006                                    0.0   
...                                          ...   
W01001954                                    1.0   
W01001955                                    0.0   
W01001956                                    3.0   
W01001957                                    0.0   
W01001958                                    0.0   

  

In [510]:
final_df.columns = [c.replace("Solid fuel", "biomass") for c in final_df.columns]
final_df.columns = [c.replace("solid fuel", "biomass") for c in final_df.columns]
rename_dict = {}
for c in current_categories:
    if potential:
        rename_dict["Mean "+c.lower()] = "Average heat demand after energy efficiency measures for "+c.lower()+" (kWh)"
    else:
        rename_dict["Mean "+c.lower()] = "Average heat demand before energy efficiency measures for "+c.lower()+" (kWh)"


rename_dict

{'Mean detached gas boiler': 'Average heat demand before energy efficiency measures for detached gas boiler (kWh)',
 'Mean detached resistance heating': 'Average heat demand before energy efficiency measures for detached resistance heating (kWh)',
 'Mean detached oil boiler': 'Average heat demand before energy efficiency measures for detached oil boiler (kWh)',
 'Mean detached biomass boiler': 'Average heat demand before energy efficiency measures for detached biomass boiler (kWh)',
 'Mean semi-detached gas boiler': 'Average heat demand before energy efficiency measures for semi-detached gas boiler (kWh)',
 'Mean semi-detached resistance heating': 'Average heat demand before energy efficiency measures for semi-detached resistance heating (kWh)',
 'Mean semi-detached oil boiler': 'Average heat demand before energy efficiency measures for semi-detached oil boiler (kWh)',
 'Mean semi-detached biomass boiler': 'Average heat demand before energy efficiency measures for semi-detached biomass

In [511]:
final_df.rename(columns=rename_dict, inplace=True)

In [512]:
rename_dict = {}
number_2011 = [c for c in final_df.columns if "2011" in c]

for c in number_2011:
    for existing_c in current_categories:
#         print(existing_c)
        if existing_c.lower() in c.lower():
            rename_dict[c] = "Number of " + existing_c.lower() + " in 2011"
            
number_2018 = [c for c in final_df.columns if "2018" in c]
for c in number_2018:
    for existing_c in current_categories:
#         print(existing_c)
        if existing_c.lower() in c.lower():
            rename_dict[c] = "Number of " + existing_c.lower()+ " in 2018"
rename_dict

{'Number of detached gas boiler in 2011': 'Number of detached gas boiler in 2011',
 'Number of detached resistance heating in 2011': 'Number of detached resistance heating in 2011',
 'Number of detached oil boiler in 2011': 'Number of detached oil boiler in 2011',
 'Detached biomass boiler 2011': 'Number of detached biomass boiler in 2011',
 'Number of semi-detached gas boiler in 2011': 'Number of semi-detached gas boiler in 2011',
 'Number of semi-detached resistance heating in 2011': 'Number of semi-detached resistance heating in 2011',
 'Number of semi-detached oil boiler in 2011': 'Number of semi-detached oil boiler in 2011',
 'Semi-detached biomass boiler 2011': 'Number of semi-detached biomass boiler in 2011',
 'Number of terraced gas boiler in 2011': 'Number of terraced gas boiler in 2011',
 'Number of terraced resistance heating in 2011': 'Number of terraced resistance heating in 2011',
 'Number of terraced oil boiler in 2011': 'Number of terraced oil boiler in 2011',
 'Terrace

In [513]:
final_df.rename(columns=rename_dict, inplace=True)

In [514]:
final_df

N_Households 2011             Rurality   MSOA11CD    LAD11CD  \
LSOA11CD                                                                  
E01000001                876  Rurality_Urban >10K  E02000001  E09000001   
E01000002                830  Rurality_Urban >10K  E02000001  E09000001   
E01000003                817  Rurality_Urban >10K  E02000001  E09000001   
E01000005                467  Rurality_Urban >10K  E02000001  E09000001   
E01000006                543  Rurality_Urban >10K  E02000017  E09000002   
...                      ...                  ...        ...        ...   
W01001954                637  Rurality_Urban >10K  W02000372  W06000015   
W01001955               1153  Rurality_Urban >10K  W02000192  W06000011   
W01001956                803  Rurality_Urban >10K  W02000190  W06000011   
W01001957                411  Rurality_Urban >10K  W02000192  W06000011   
W01001958                836  Rurality_Urban >10K  W02000192  W06000011   

                Local Authority  Detached No central heating 2011  \
LSOA11CD                                                            
E01000001        City of London                               0.0   
E01000002        City of London                               0.0   
E01000003        City of London                               0.0   
E01000005        City of London                               0.0   
E01000006  Barking and Dagenham                               2.0   
...                         ...                               ...   
W01001954               Cardiff                               0.0   
W01001955               Swansea                               0.0   
W01001956               Swansea                               1.0   
W01001957               Swansea                               0.0   
W01001958               Swansea                               0.0   

           Number of detached gas boiler in 2011  \
LSOA11CD                                           
E01000001                                    0.0   
E01000002                                    0.0   
E01000003                                    0.0   
E01000005                                    1.0   
E01000006                                   26.0   
...                                          ...   
W01001954                                  274.0   
W01001955                                   10.0   
W01001956                                  259.0   
W01001957                                    3.0   
W01001958                                    8.0   

           Number of detached resistance heating in 2011  \
LSOA11CD                                                   
E01000001                                            0.0   
E01000002                                            0.0   
E01000003                                            0.0   
E01000005                                            0.0   
E01000006                                            1.0   
...                                                  ...   
W01001954                                            0.0   
W01001955                                            6.0   
W01001956                                            3.0   
W01001957                                            1.0   
W01001958                                            0.0   

           Number of detached oil boiler in 2011  \
LSOA11CD                                           
E01000001                                    0.0   
E01000002                                    0.0   
E01000003                                    0.0   
E01000005                                    0.0   
E01000006                                    0.0   
...                                          ...   
W01001954                                    1.0   
W01001955                                    0.0   
W01001956                                    3.0   
W01001957                                    0.0   
W01001958                                    0.0   

  

In [515]:
final_df.to_csv(saving_path+os.path.sep+"LSOAs_in_England_Wales_before_EE_heat_demand.csv")
number_epc_df.to_csv(saving_path+os.path.sep+"Number_EPCs_LSOAs_in_England_Wales_before_EE_heat_demand.csv")

In [501]:
final_df.to_csv(saving_path+os.path.sep+output_file_name+".csv")

number_epc_df.to_csv(saving_path+os.path.sep+"Number_EPCs_"+output_file_name+".csv")